# Restaurant Recommendations Systems using Yelp Dataset

###### This project aims to implement a restaurant recommendation systems by getting customer review data from the public Yelp dataset. The system will use stars and favorites data to determine similarities between customers and will recommend restaurants based on those information.

## Part 1: Data collection and cleaning

###### Parsing the JSON data file from yelp using the ijson library, which reads a 5 GB+ file in a split second. Then make a dictionary where the key is the User ID and the value is the number of reviews that user gives. We are doing this to get the most useful data from users that review the most restaurants since the entire dataset is too big to use effectively.

In [52]:
# importing libraries
import ijson
import decimal
from collections import defaultdict

def parse_json_user(json_filename):
    data_dict = defaultdict(list)
    n = 0
    count = 0
    with open(json_filename, 'rb') as input_file:
        # load json iteratively
        parser = ijson.parse(input_file, multiple_values=True)
        for prefix, event, value in parser:
            if n >= 30000:
                # sort to get the users with most review first
                return sorted(data_dict, key=lambda x:data_dict[x], reverse=True)
            # obtain the review count and its respective user ID
            if prefix == 'review_count':
                count = int(value)
                n += 1
            if prefix == 'user_id':
                user_id = value
                # make a dictionary with userID as the key and review count as the value
                data_dict[user_id].append(count)

user_datadict = parse_json_user("yelp_dataset/yelp_academic_dataset_user.json")
print(user_datadict)

['7xQYlgl7YKX8RfbB5SdK_Q', 'OXnmwRYK5etGqUAnj3CTbg', 'VpREWOjt5Pna6OIgXI9Jcg', 'bGREVtD0aDERKe5k4d5Zkg', 'rinyHgUZ-8Vk6zEGAoODpQ', 'X0pYbaeyptPwbRksy7rGHA', 'J_jerijrgPX7CRvG2mMWMw', 'S_gfT9oI-vVmp-LPBdHT1A', 'qhw0RjIGgStx7s4mjqkWFQ', 'US4XWHCxjPA07Q_MESq0cQ', 'DSDL_v5dvLOIJ-o5sRhz4w', 'zjcN27kCVeK8K2ONe9Qt4g', 'r_N0g_6ouOK2YXrHDeOWkg', 'cUBQOp3_XDBdSHn7EUspkQ', 'FVk12H4Cz4DkRzl8N5-PGQ', 'Qc6UTFaDLIjvTKIOh2E9zw', 'XhyhVUB7hMuyRVGb3mACpQ', 'Y2jaBiziIx5nd6xnzLZOUg', 'tAHMuChEo1Fs6qaRJ7pPng', '2WnXYQFK0hXEoTxPtV2zvg', 'GcEaEhVBp0DcAbgdPw41eg', 'bv4Mjlh7Ng4xACwi5CNtAA', 'OoFKiEKyw97IWhbecLHSwQ', 'PLM6psqBZ1Gg3v6SunxCQg', 'SJFMj23zYMUbVggDWvwFaQ', 'BvnchfgvNbzeXvz-7sHVpQ', 'IoEJBuQ8mhFgxvQS8E8eDw', 'Sf8yKmUnsTk2HNzLpSxzTA', 'cDQrXXx3tAJswx0HouTV2A', 'upKCYdxGuw2oUtbUQuQRCg', 'nlmdh1lh0XyPecHvcdfTHQ', 'xdCTp-EPp6F80oabkpBB4w', 'KHh28X_iuAkSUyUzXWa9cQ', 'Q1WRnsP8net9hJ-IkU9-4A', '6snhyTl6iU8ti-1EIJuFvQ', 'FEmnXLOdG6OcdGXjRth28A', 'TLVutP9yzAkJVDIK5oVlNA', 'hZ_tIZhMhIYd126yoxssvQ', 'HAAdELyXWv

###### Import in another JSON file that contains the review from each customer. We will take the reviews of the 10000 people in the list above, no matter what the restaurant is. Then we will make a dictionary that contains the user's name as a key, and the business ID and its respective review (# of stars) as the value.

In [53]:
import ijson
import decimal

def parse_json_review(json_filename):
    data_dict = defaultdict(list)
    n = 0
    with open(json_filename, 'rb') as input_file:
        # load json iteratively
        parser = ijson.parse(input_file, multiple_values=True)
        for prefix, event, value in parser:
            if n >= 80000:
                return data_dict
            if prefix == 'user_id':
                user_id = value
            if prefix == 'business_id':
                busi_id = value
            if prefix == 'stars':
                stars = float(value)
                n += 1
#                 print(user_id, busi_id, stars)
                if user_id in user_datadict:
                    data_dict[user_id].append([busi_id, stars])

reviews_datadict = parse_json_review("yelp_dataset/yelp_academic_dataset_review.json")
print(reviews_datadict)

###### Import another JSON file that contains the businesses' information. We use this file to convert the business ID into a readable restaurant names

In [42]:
def parse_json_business(json_filename):
    data_dict = {}
    n = 0
    with open(json_filename, 'rb') as input_file:
        # load json iteratively
        parser = ijson.parse(input_file, multiple_values=True)
        for prefix, event, value in parser:
            if n >= 50000:
                return data_dict
            if prefix == 'business_id':
                busi_id = value
            if prefix == 'name':
                name = value
                n += 1
                data_dict[busi_id] = name

names_datadict = parse_json_business("yelp_dataset/yelp_academic_dataset_business.json")
print(names_datadict)

{'Pns2l4eNsfO8kk83dixA6A': 'Abby Rappoport, LAC, CMQ', 'mpf3x-BjTdTEA3yCZrAYPw': 'The UPS Store', 'tUFrWirKiKi_TAnsVWINQQ': 'Target', 'MTSW4McQd7CbVtyjqoe9mw': 'St Honore Pastries', 'mWMc6_wTdE0EUBKIGXDVfA': 'Perkiomen Valley Brewery', 'CF33F8-E6oudUQ46HnavjQ': 'Sonic Drive-In', 'n_0UpQx1hsNbnPUSlodU8w': 'Famous Footwear', 'qkRM_2X51Yqxk3btlwAQIg': 'Temple Beth-El', 'k0hlBqXX-Bt0vf1op7Jr1w': "Tsevi's Pub And Grill", 'bBDDEgkFA1Otx9Lfe7BZUQ': 'Sonic Drive-In', 'UJsufbvfyfONHeWdvAHKjA': 'Marshalls', 'eEOYSgkmpB90uNA7lDOMRA': 'Vietnamese Food Truck', 'il_Ro8jwPlHresjw9EGmBg': "Denny's", 'jaxMSoInw8Poo3XeMJt8lQ': 'Adams Dental', '0bPLkL0QhhPO5kt1_EXmNQ': "Zio's Italian Market", 'MUTTqe8uqyMdBl186RmNeA': 'Tuna Bar', 'rBmpy_Y1UbBx8ggHlyb7hA': 'Arizona Truck Outfitters', 'M0XSSHqrASOnhgbWDJIpQA': 'Herb Import Co', '8wGISYjYkE2tSqn3cDMu8A': 'Nifty Car Rental', 'ROeacJQwBeh05Rqg7F6TCg': 'BAP', 'WKMJwqnfZKsAae75RMP6jA': 'Roast Coffeehouse and Wine Bar', 'qhDdDeI3K4jy2KyzwFN53w': 'Barnes & Noble 

In [43]:
for value in reviews_datadict.values():
    for i in value:
        if i[0] in names_datadict:
            i[0] = names_datadict[i[0]]
reviews_datadict

defaultdict(list,
            {'r3zeYsv1XFBRA4dJpL78cw': [['The Voodoo Bone Lady Tours', 5.0]],
             'smOvOajNG0lS4Pq7d8g4JQ': [["LaScala's", 4.0]],
             '4Uh27DgGzsp6PqrH913giQ': [['BK Tacos', 4.0],
              ['Taqueria Pico De Gallo', 4.0]],
             'j2wlzrntrbKwyOcOiB3l3w': [['Olio', 4.0],
              ['Home Wine Kitchen', 4.0]],
             'IQsF3Rc6IgCzjVV9DE8KXg': [['Good Karma Cafe', 5.0]],
             'Ohhrhu1RkqfVciIVx_W5HQ': [['Ted Drewes', 5.0],
              ['Pi Pizzeria - Delmar Loop', 4.0]],
             'vrKkXsozqqecF3CW4cGaVQ': [['The N Crowd', 5.0], ['Penang', 4.0]],
             'zoBajEyVA0z4IjbFsMJksg': [['Barbecue and Bourbon', 4.0]],
             'clWLI5OZP2ad25ugMVI8gg': [['Thai Place Restaurant', 5.0]],
             '3MpDvy5gEdsbZh9-p92dHg': [["Sweet Cece's", 4.0],
              ['Edgehill Cafe', 4.0],
              ['Foggy Bottom Canoe Rocks', 4.0],
              ["Newk's Eatery", 4.0],
              ['Days Inn by Wyndham New Orlean

###### Arrange the data in the way that each row is a each user, and all restaurants are in each columns. The rating of a restaurant x of a user y will fall in the cell (x,y) of the dataframe. I also printed the restaurant counts and user counts to see approximately what I am working with.

In [44]:
import pandas as pd
reviews_list = []
for key, value in reviews_datadict.items():
    for i in value:
        reviews_list.append([key, i[0], i[1]])
ratings = pd.DataFrame(reviews_list, columns = ['User_id', 'Restaurant', 'Stars'])
ratings
print('Restaurant counts:', (ratings.groupby(['Restaurant']).count()).shape[0])
print('user counts:', (ratings.groupby(['User_id']).count()).shape[0])

Restaurant counts: 4199
user counts: 11297


In [45]:
ratings

User_id  \
0      r3zeYsv1XFBRA4dJpL78cw   
1      smOvOajNG0lS4Pq7d8g4JQ   
2      4Uh27DgGzsp6PqrH913giQ   
3      4Uh27DgGzsp6PqrH913giQ   
4      j2wlzrntrbKwyOcOiB3l3w   
...                       ...   
17338  Gza5FyPBK631DujKWMkdnA   
17339  CcOgdfEJxgrxTAwag5k18Q   
17340  NBJjQ7-02DfpLkmVYmQXxw   
17341  -uipbMpNvnY3YSWiEJ3D4g   
17342  LeId4r8i9KxtyyWuSqEHfg   

                                              Restaurant  Stars  
0                             The Voodoo Bone Lady Tours    5.0  
1                                              LaScala's    4.0  
2                                               BK Tacos    4.0  
3                                 Taqueria Pico De Gallo    4.0  
4                                                   Olio    4.0  
...                                                  ...    ...  
17338                                        Bravo Pizza    5.0  
17339                                           Jiallo's    4.0  
17340                                   Beef 'O' Brady's    3.0  
17341                                     Symphony Nails    5.0  
17342  DoubleTree by Hilton Hotel Philadelphia Center...    3.0  

[17343 rows x 3 columns]

###### Make a pivot table where each restaurant takes a column and each user takes a row. The review of user (y) of the restaurant (x) will be in cell (x,y) No review will automatically be counted as 0.

In [46]:
import numpy as np

ratings_pivot = pd.pivot_table(ratings, index='User_id', columns='Restaurant', values='Stars', aggfunc=np.mean)
ratings_pivot = ratings_pivot.fillna(0)
ratings_pivot

Restaurant              'feine  1 Tippling Place  \
User_id                                            
---2PmXbF47D870stH1jqA     0.0               0.0   
--ccVMj2PN6Z9qtdOdlung     0.0               0.0   
--sL83g4I7GhwcBRQjKS6A     0.0               0.0   
-0IiMAZI2SsQ7VmyzJjokQ     0.0               0.0   
-0vutwuE36iYMqM2wHaStQ     0.0               0.0   
...                        ...               ...   
zxMo7emoqvWavJRtJF_9rw     0.0               0.0   
zxeXnjqmlrAspfk17LSZCg     0.0               0.0   
zxkpvlYCpeHEuky4MKe3_Q     0.0               0.0   
zyNrXvJyYdC34tS6BcCykA     0.0               0.0   
zzT0pSbiaNAPL171kwnvjA     0.0               0.0   

Restaurant              1-275 Rest Area Manatee County Mile 7  \
User_id                                                         
---2PmXbF47D870stH1jqA                                    0.0   
--ccVMj2PN6Z9qtdOdlung                                    0.0   
--sL83g4I7GhwcBRQjKS6A                                    0.0   
-0IiMAZI2SsQ7VmyzJjokQ                                    0.0   
-0vutwuE36iYMqM2wHaStQ                                    0.0   
...                                                       ...   
zxMo7emoqvWavJRtJF_9rw                                    0.0   
zxeXnjqmlrAspfk17LSZCg                                    0.0   
zxkpvlYCpeHEuky4MKe3_Q                                    0.0   
zyNrXvJyYdC34tS6BcCykA                                    0.0   
zzT0pSbiaNAPL171kwnvjA                                    0.0   

Restaurant              101 Taiwanese Cuisine  10th Street Italian  \
User_id                                                              
---2PmXbF47D870stH1jqA                    0.0                  0.0   
--ccVMj2PN6Z9qtdOdlung                    0.0                  0.0   
--sL83g4I7GhwcBRQjKS6A                    0.0                  0.0   
-0IiMAZI2SsQ7VmyzJjokQ                    0.0                  0.0   
-0vutwuE36iYMqM2wHaStQ                    0.0                  0.0   
...                                       ...                  ...   
zxMo7emoqvWavJRtJF_9rw                    0.0                  0.0   
zxeXnjqmlrAspfk17LSZCg                    0.0                  0.0   
zxkpvlYCpeHEuky4MKe3_Q                    0.0                  0.0   
zyNrXvJyYdC34tS6BcCykA                    0.0                  0.0   
zzT0pSbiaNAPL171kwnvjA                    0.0                  0.0   

Restaurant              12 South Winter Warmer  12 South Yoga  1200 Chophouse  \
User_id                                                                         
---2PmXbF47D870stH1jqA                     0.0            0.0             0.0   
--ccVMj2PN6Z9qtdOdlung                     0.0            0.0             0.0   
--sL83g4I7GhwcBRQjKS6A                     0.0            0.0             0.0   
-0IiMAZI2SsQ7VmyzJjokQ                     0.0            0.0             0.0   
-0vutwuE36iYMqM2wHaStQ                     0.0            0.0             0.0   
...                                        ...            ...             ...   
zxMo7emoqvWavJRtJF_9rw                     0.0            0.0             0.0   
zxeXnjqmlrAspfk17LSZCg                     0.0            0.0             0.0   
zxkpvlYCpeHEuky4MKe3_Q                     0.0            0.0             0.0   
zyNrXvJyYdC34tS6BcCykA                     0.0            0.0             0.0   
zzT0pSbiaNAPL171kwnvjA                     0.0            0.0             0.0   

Restaurant              12th & Porter  1501 Linden Manor Bed & Breakfast  ...  \
User_id                                                                   ...   
---2PmXbF47D870stH1jqA            0.0                                0.0  ...   
--ccVMj2PN6Z9qtdOdlung            0.0                                0.0  ...   
--sL83g4I7GhwcBRQjKS6A            0.0                                0.0  ...   
-0IiMAZI2SsQ7VmyzJjokQ            0.0                                0.0  ...   
-0vutwuE36iYMqM2wHaStQ    

## Part 2: Building the recommendation algorithm

###### This part includes scaling the pivot table data using Standardscaler(), then calculating the dot products and sorting it from highest to lowest. The restaurant with highest dot product means it is more similar to the item we are comparing to. Getting the first 5 of the sorted list, we obtain the recommendations

In [59]:
# SCALED
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.preprocessing import StandardScaler
from sklearn.utils.extmath import randomized_svd
from sklearn.decomposition import TruncatedSVD

sc_X = StandardScaler()
scaled_df = sc_X.fit_transform(ratings_pivot)

new_df = pd.DataFrame(scaled_df, columns = ratings_pivot.columns, index = ratings_pivot.index)
new_df

def get_item_recommendations(compare_item, df, num_recom):
    recs = []
    for item in df.columns.values:
        if item != compare_item:
            recs.append((np.dot(df[compare_item],df[item]), item))
    recs.sort(reverse = True)
    final_rec = [(i[1], i[0]) for i in recs]
    return final_rec[:num_recom]

item = '10th Street Italian'

print(len(ratings_pivot[ratings_pivot[item] != 0]))
print(f"Items similar to item {item}: {get_item_recommendations(item,new_df,5)}")

1
Items similar to item 10th Street Italian: [('Kitchen K', 7832.7721265846385), ('Rue 13', 6389.959858059617), ('Brio Italian Grille', 3414.397989046483), ("Landry's Seafood House", 2340.922185154315), ('Pi Pizzeria - Delmar Loop', 1687.8857647955563)]


In [57]:
# NOT SCALED
item = '10th Street Italian'

print(len(ratings_pivot[ratings_pivot[item] != 0]))
print(f"Items similar to item {item}: {get_item_recommendations(item,ratings_pivot,5)}")

1
Items similar to item 10th Street Italian: [('Kitchen K', 20.0), ('Rue 13', 16.0), ('Pi Pizzeria - Delmar Loop', 16.0), ('Brio Italian Grille', 16.0), ("Landry's Seafood House", 8.0)]


###### Sometimes the recommendation system does not work if that restaurant is only reviewed by one person in our dataset. A negative dot product is a sign of that. The way to solve it would be to use more data (We are only using a little bit right now), but my computer cannot handle it :(

## Part 3: Other applications

In [129]:
import ijson
import decimal

def parse_json_review(json_filename):
    data_dict = defaultdict(list)
    n = 0
    gmapid=0
    with open(json_filename, 'rb') as input_file:
        # load json iteratively
        parser = ijson.parse(input_file, multiple_values=True)
        for prefix, event, value in parser:
            if n >= 30000:
                return data_dict
            if prefix == 'user_id':
                user_id = value
            if prefix == 'rating':
                stars = float(value)
            if prefix == 'gmap_id':
                gmapid = value
                n += 1
                if [gmapid, stars] not in data_dict[user_id]:
                    data_dict[user_id].append([gmapid, stars])

reviews_datadict = parse_json_review("review-Oregon.json")
print(reviews_datadict)

defaultdict(<class 'list'>, {'108990823942597776781': [['0x80dce9997c8d25fd:0xc6c81c1983060cbc', 5.0]], '113177950518394018158': [['0x89d0ba60af135b2f:0xd548538d7a3e2b8', 5.0]], '108990308575939133390': [['0x89d0ba60af135b2f:0xd548538d7a3e2b8', 5.0]], '107483764979365052258': [['0x89d0ba60af135b2f:0xd548538d7a3e2b8', 5.0]], '103367354489635000443': [['0x89d0ba60af135b2f:0xd548538d7a3e2b8', 5.0]], '108987872130068567793': [['0x549576c32c7ce82d:0x166266dbfadf6660', 5.0]], '106007946076735422938': [['0x549576c32c7ce82d:0x166266dbfadf6660', 5.0]], '107511507221331972306': [['0x549576c32c7ce82d:0x166266dbfadf6660', 5.0]], '105191089114919170606': [['0x549576c32c7ce82d:0x166266dbfadf6660', 5.0]], '116028080723136509441': [['0x549576c32c7ce82d:0x166266dbfadf6660', 5.0]], '100310839899766895462': [['0x549576c32c7ce82d:0x166266dbfadf6660', 5.0]], '112304066206041687598': [['0x54bfff5952aad583:0xad7afdc825730614', 5.0]], '107311292304999908474': [['0x54bfff5952aad583:0xad7afdc825730614', 5.0]], 

In [130]:
import ijson
import decimal

def parse_json_business(json_filename):
    data_dict = defaultdict(list)
    n = 0
    gmapid=0
    name=0
    with open(json_filename, 'rb') as input_file:
        # load json iteratively
        parser = ijson.parse(input_file, multiple_values=True)
        for prefix, event, value in parser:
            if n >= 300000:
                return data_dict
            if prefix == 'name':
                name = value
            if prefix == 'gmap_id':
                gmapid = value
            n += 1
            if name != 0:
                data_dict[gmapid] = name
    return data_dict

names_datadict = parse_json_business("meta-Oregon.json")
print(names_datadict)

defaultdict(<class 'list'>, {0: 'iPolish Nails Spa', '0x80dce9997c8d25fd:0xc6c81c1983060cbc': 'Karens Country Confections, LLC', '0x89d0ba60af135b2f:0xd548538d7a3e2b8': 'E & L General Contractors Inc', '0x549576c32c7ce82d:0x166266dbfadf6660': 'McDonald Orthodontics', '0x54bfff5952aad583:0xad7afdc825730614': "Donatello's at Marion Forks", '0x54bf0922053d25ed:0x73bbe9954ead56b2': 'Rock Garden', '0x5494cca5bc6219af:0x138ee88bb56205ad': 'Creative Science School at Clark', '0x5495a1af3e6d8817:0xb7d571c69e486f66': 'The Dentist Off Main', '0x54956273f74cdad5:0x6e79bcd944e0855d': 'Precision Diesel Truck & Equipment Repair', '0x5495a64583512b19:0x1583bc844cde3979': 'Stutzman Environmental Products', '0x5495644ebe4a9fc3:0x87a932a2cef20e8c': 'Bridgetown Optometric Associates', '0x54950f43d1e91d6f:0x2b94e43d1c23a5b4': 'The Dalles Disposal Service', '0x54961e77484f68c1:0x8b484a4ed600c486': 'Mud Hollow', '0x54bd87d2e50d1ac3:0x7e01c204e0670647': 'U-Haul Moving & Storage of The Dalles', '0x54961d05f04

In [162]:
import collections
for value in reviews_datadict.values():
    for i in value:
        if i[0] in names_datadict:
            i[0] = names_datadict[i[0]]
places = []
for value in reviews_datadict.values():
    for i in value:
        places.append(i[0])
res = collections.Counter(places)
res.most_common()

[('Salon Spa', 347),
 ('Murrayhill Chiropractic Center', 272),
 ('Sacramento DJ Service', 257),
 ('Schwan Food Co', 236),
 ('L & G Auto Repair', 215),
 ("Donatello's at Marion Forks", 188),
 ('First Baptist Church', 164),
 ('Central Electric Cooperative, Inc.', 148),
 ('Lichun (Susan) Lee, Keller Williams Sunset Corridor', 138),
 ('M&M INVESTMENT CARS', 128),
 ('Xfinity', 126),
 ('Back to the Basics Massage', 118),
 ('Audi Volkswagen Parts - Location closed - Website only', 115),
 ('Precision Diesel Truck & Equipment Repair', 114),
 ('de la tierra, inc.', 108),
 ('Sound Pacific Resources', 105),
 ('Max Muscle Nutrition', 103),
 ('Bishops Store House', 100),
 ('Sweet Confections by LaTasha', 98),
 ('DM Glass', 95),
 ('Twin Peaks Offroad', 90),
 ('TLG ISLAND STYLE BBQ', 86),
 ('Empire Concrete Cutting', 85),
 ('Bruce & Dana Inc', 85),
 ('Youth Outreach Center Public Art', 85),
 ('Ralph Gracie Brazilian Jiu-Jitsu (BJJ) - Bend', 84),
 ('PENSOLE Footwear Design Academy', 83),
 ('Gonzalez Gl

In [166]:
import pandas as pd

reviews_list = []
for key, value in reviews_datadict.items():
    for i in value:
        reviews_list.append([key, i[0], i[1]])
ratings = pd.DataFrame(reviews_list, columns = ['User_id', 'Place', 'Stars'])
ratings
print('Place counts:', (ratings.groupby(['Place']).count()).shape[0])
print('user counts:', (ratings.groupby(['User_id']).count()).shape[0])

ratings_pivot = pd.pivot_table(ratings, index='User_id', columns='Place', values='Stars', aggfunc=np.mean)
ratings_pivot = ratings_pivot.fillna(0)
ratings_pivot

sc_X = StandardScaler()
scaled_df = sc_X.fit_transform(ratings_pivot)

new_df = pd.DataFrame(scaled_df, columns = ratings_pivot.columns, index = ratings_pivot.index)
new_df

def get_item_recommendations(compare_item, df, num_recom):
    recs = []
    for item in df.columns.values:
        if item != compare_item:
            recs.append((np.dot(df[compare_item],df[item]), item))
    recs.sort(reverse = True)
    final_rec = [(i[1], i[0]) for i in recs if i[0] != 0]
    return final_rec[:num_recom]

item = 'Central Electric Cooperative, Inc.'

print(f"Items similar to item {item}: {get_item_recommendations(item,ratings_pivot,5)}")

Place counts: 1487
user counts: 21256
Items similar to item Central Electric Cooperative, Inc.: [("Itiel's Carports & Metal Buildings LLC", 25.0), ('Tesla Destination Charger', 20.0), ('U-Haul Storage of The North Coast', 15.0)]


## Part 4: Extra stuffs that did not work

In [296]:
import googlemaps

api_key = ''
gmaps = googlemaps.Client(key=api_key)

place_name = 'Sambi'
place_details = gmaps.places(place_name)
place_details

place_id = place_details['results'][0]['place_id']
place = gmaps.place(place_id)
print(place['result']['reviews'])

ApiError: REQUEST_DENIED (This API project is not authorized to use this API.)

In [5]:
from selenium import webdriver
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.common.action_chains import ActionChains
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import ElementNotVisibleException
from selenium.webdriver.common.by import By
from selenium.common.exceptions import TimeoutException
from bs4 import BeautifulSoup

driver = webdriver.Chrome(ChromeDriverManager().install())

location = "97223"

query = "food near " + location
driver.get("https://www.google.com/search?q=" + query)
wait = WebDriverWait(driver, 10)
ActionChains(driver).move_to_element(wait.until(EC.element_to_be_clickable(
    (By.XPATH, "//a[contains(@href, '/search?tbs')]")))).perform()
wait.until(EC.element_to_be_clickable(
    (By.XPATH, "//a[contains(@href, '/search?tbs')]"))).click()
names = []
reviews = []
for name in driver.find_elements(By.XPATH, "//div[@aria-level='3']"):
    names.append(name.text)
for review in driver.find_elements(By.CSS_SELECTOR, "span.yi40Hd.YrbPuc"):
    reviews.append(review.text)


/var/folders/j6/14l5ybgs2cz_vt6rg313741w0000gp/T/ipykernel_21987/3663799593.py:11: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


KeyboardInterrupt: 

In [9]:
reviews = [i for i in reviews if i != '']
print(names, reviews)
print(len(names), len(reviews))

['Din Tai Fung', "Banning's Restaurant & Pie House", 'Sushi Hana', 'Thai Delicious Restaurant', 'The Mac', 'Moonlight Grill & Deli Tigard', 'Mandarin Palace Restaurant / Lounge', 'Thirsty Lion Gastropub', 'Cascadia Restaurant & Bar', 'Stripes -All American Food', 'Broder Söder', "Ezell's Famous Chicken", 'House of Teriyaki', 'Honey Spicy - Korean Fusion Restaurant', 'Mugen Noodle Bar', 'Smoke Squad', 'Mongolian BBQ', 'Mazatlan Mexican Restaurant', 'Gators Pub & Eatery', 'Koba Grill'] ['4.5', '4.5', '4.0', '4.6', '3.9', '4.7', '4.0', '4.3', '4.1', '4.0', '4.6', '3.8', '4.6', '4.5', '4.7', '4.6', '4.4', '4.3', '4.2', '4.1']
20 20
